In [1]:
!nvidia-smi

Sat Aug  7 14:43:59 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.42.01    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   41C    P0    26W / 250W |      0MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
!pip install torchaudio
!pip install audiomentations[extras]
!pip install transformers

In [3]:
import os
os.chdir("./drive/MyDrive/AudioTech/code")

In [4]:
!ls

data  examples	kaldi_model  kaldi_model_daanzu_20200905_1ep-biglm.zip	model


In [5]:
from torchaudio.datasets import LIBRISPEECH
dataloader = LIBRISPEECH(root="./data",url="train-clean-100")

In [6]:
for item in dataloader:
  break

In [7]:
len(item)

6

In [8]:
wav, sr, text, speaker_id, chapter_id, text_id = item

In [9]:
import librosa
import numpy as np

In [10]:
noisy_wav = wav.numpy().flatten() + np.random.randn(wav.shape[1]) * 0.01
target_sr = 16000

In [11]:
from IPython.display import Audio, display
import torch
def play_audio(waveform, sample_rate):
  if isinstance(waveform,torch.Tensor):
    waveform = waveform.numpy()

  num_channels, num_frames = waveform.shape
  if num_channels == 1:
    display(Audio(waveform[0], rate=sample_rate))
  elif num_channels == 2:
    display(Audio((waveform[0], waveform[1]), rate=sample_rate))
  else:
    raise ValueError("Waveform with more than 2 channels are not supported.")

In [12]:
wav.shape

torch.Size([1, 225360])

In [13]:
play_audio(noisy_wav.reshape((1,len(noisy_wav))),sr)

In [14]:
from torch.utils.data import Dataset
from torchaudio.transforms import MelSpectrogram
from audiomentations import Compose, AddGaussianNoise, PitchShift, Gain, Shift, ClippingDistortion, TimeMask, Mp3Compression
from torchaudio.datasets import LIBRISPEECH

dataloader = LIBRISPEECH(root="./data",url="train-clean-100")

class AudioTechDataset(Dataset):
  TRANSFORM_STEPS = Compose([
          # AddGaussianNoise(min_amplitude=0.01, max_amplitude=0.01, p=0.5),
          # PitchShift(min_semitones=-1, max_semitones=1, p=0.5),
          # Gain(min_gain_in_db=-12, max_gain_in_db=12, p=0.5),
      ])
  AUGMENT_STEPS = Compose([
        TimeMask(min_band_part=0.05, max_band_part=0.05, fade=False, p=1),
        # AddGaussianNoise(min_amplitude=0.0001, max_amplitude=0.0005, p=0.5),
        TimeMask(min_band_part=0.05, max_band_part=0.05, fade=False, p=1),
        TimeMask(min_band_part=0.05, max_band_part=0.05, fade=False, p=1),
        TimeMask(min_band_part=0.05, max_band_part=0.05, fade=False, p=1),
        TimeMask(min_band_part=0.05, max_band_part=0.05, fade=False, p=1),
        TimeMask(min_band_part=0.05, max_band_part=0.05, fade=False, p=1),
        TimeMask(min_band_part=0.05, max_band_part=0.05, fade=False, p=1),
        # Shift(min_fraction=-0.1, max_fraction=0.1, p=1),
        ClippingDistortion(min_percentile_threshold=50, max_percentile_threshold=50, p=1),
        Mp3Compression(min_bitrate= 8, max_bitrate= 8, backend= "pydub", p=1),
        

    ])

  def __init__(self,librispeech,augment=False,transform=None):
    self.librispeech = librispeech
    self.augment = augment
    self.transform = transform
  
  def __len__(self):
    return len(self.librispeech)

  def format_wav(self,target_wav,sr,seconds=15):
    if target_wav.shape[1] / sr > seconds:
          target_wav = target_wav[:, :seconds * sr]
    elif target_wav.shape[1] / sr < seconds:
          padding = torch.zeros(1, seconds * sr - target_wav.shape[1])
          target_wav = torch.cat((target_wav, padding), dim = 1)
    return target_wav

  def transform_wav(self,target_wav,sr):
      # target_wav = self.TRANSFORM_STEPS(samples=np.array(target_wav), sample_rate=sr)
      # return torch.from_numpy(target_wav)
      return target_wav
  
  def augment_wav(self,target_wav,sr):
    augmented_wav = self.AUGMENT_STEPS(samples=np.array(target_wav.flatten()),sample_rate=sr)
    return torch.from_numpy(augmented_wav.reshape((1,augmented_wav.shape[0])))

  def __getitem__(self,idx):
    # getting item
    long_target_wav, target_sr, text, speaker_id, chapter_id, text_id = self.librispeech[idx]
    # print(text)
    target_wav = self.format_wav(long_target_wav,target_sr)
    # creating mel spectogrammer
    spectogrammer = MelSpectrogram(sample_rate=target_sr,n_mels=128)

    # correctly format wav
    target_spec = spectogrammer(target_wav)

    # transform (always transform to get input data)
    transformed_wav = self.transform_wav(target_wav,target_sr)
    transformed_spec = spectogrammer(transformed_wav)

    # augment
    if self.augment:
      augmented_wav = self.augment_wav(transformed_wav,target_sr)
      augmented_spec = spectogrammer(augmented_wav)
      return target_wav, target_spec, augmented_wav, augmented_spec, target_sr, speaker_id, text_id
    else:
      return target_wav, target_spec, transformed_wav, transformed_spec, sr, speaker_id, text_id

for target_wav, target_spec, input_wav, input_spec, sr, speaker_id, text_id in AudioTechDataset(dataloader, augment=True,transform=True):
  break 

original_speaker_id = speaker_id
original_text_id = text_id
# for other_wav, *_, speaker_id, _ in AudioTechDataset(dataloader, augment=True,transform=True):
#   if speaker_id != original_speaker_id:
#     break 

other_wavs = []

for other_wav, *_, speaker_id, text_id in AudioTechDataset(dataloader, augment=True,transform=True):
  if speaker_id == original_speaker_id:
    if text_id != original_text_id:
      other_wavs.append(other_wav)
  if len(other_wavs)==3:
    break

/usr/local/lib/python3.7/dist-packages/torchaudio/functional/functional.py:433: UserWarning: At least one mel filterbank has all zero values. The value for `n_mels` (128) may be set too high. Or, the value for `n_freqs` (201) may be set too low.
  "At least one mel filterbank has all zero values. "
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/torchaudio/functional/functional.py:433: UserWarning: At least one mel filterbank has all zero values. The value for `n_mels` (128) may be set too high. Or, the value for `n_freqs` (201) may be set too low.
  "At least one mel filterbank has all zero values. "
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/pytho

In [15]:
import torch
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC
# from datasets import load_dataset
import soundfile as sf

processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-base-960h")
model = Wav2Vec2ForCTC.from_pretrained("facebook/wav2vec2-base-960h")

def predict_text(target_wav,sr=16000):
  # print(target_wav.shape)
  input_values = processor(np.squeeze(np.array(target_wav)), return_tensors="pt", sampling_rate=sr).input_values  # Batch size 1
  # print(input_values.shape)
  logits = model(input_values).logits
  predicted_ids = torch.argmax(logits, dim=-1)
  transcription = processor.decode(predicted_ids[0])
  return transcription

Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['wav2vec2.masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [16]:
%time
predict_text(target_wav)

CPU times: user 3 µs, sys: 1e+03 ns, total: 4 µs
Wall time: 9.78 µs


'CHAPTER ONE MISSUS RACHEL LYNDE IS SURPRISED MISSUS RACHEL LYNDE LIVED JUST WHERE THE AVONLEA MAIN ROAD DIPPED DOWN INTO A LITTLE HOLLOW FRINGED WITH ALDERS AND LADIES EARDROPS AND TRAVERSED BY A BROOK'

In [17]:
play_audio(target_wav,sr)

In [18]:
play_audio(input_wav,sr)

In [19]:
print(target_wav.shape, target_spec.shape, input_wav.shape, input_spec.shape)

torch.Size([1, 240000]) torch.Size([1, 128, 1201]) torch.Size([1, 240000]) torch.Size([1, 128, 1201])


In [20]:
os.chdir("model")

In [21]:
!ls

MaskCycleGAN-VC  Real-Time-Voice-Cloning


In [22]:
os.chdir("Real-Time-Voice-Cloning")

In [23]:
!ls

'AudioTech One-Pager.gdoc'	  requirements.txt
 demo_cli.py			  samples
 demo_toolbox.py		  synthesizer
 encoder			  synthesizer_preprocess_audio.py
 encoder_preprocess.py		  synthesizer_preprocess_embeds.py
 encoder_train.py		  synthesizer_train.py
 LICENSE.txt			  toolbox
 pa_stable_v190700_20210406.tgz   utils
 pretrained.zip			  vocoder
 pretrained.zip.1		  vocoder_preprocess.py
 pretrained.zip.2		  vocoder_train.py
 README.md


In [24]:
!pip install -r requirements.txt

Ignoring numpy: markers 'platform_system == "Windows"' don't match your environment


In [25]:
!sudo apt-get install libasound-dev portaudio19-dev libportaudio2 libportaudiocpp0
!pip install pyaudio --user

Reading package lists... Done
Building dependency tree       
Reading state information... Done
Note, selecting 'libasound2-dev' instead of 'libasound-dev'
libportaudio2 is already the newest version (19.6.0-1).
libportaudiocpp0 is already the newest version (19.6.0-1).
portaudio19-dev is already the newest version (19.6.0-1).
libasound2-dev is already the newest version (1.1.3-5ubuntu0.5).
0 upgraded, 0 newly installed, 0 to remove and 40 not upgraded.


In [26]:

#!python demo_cli.py



In [27]:
# !wget https://github.com/blue-fish/Real-Time-Voice-Cloning/releases/download/v1.0/pretrained.zip

In [28]:
# !unzip pretrained.zip

In [29]:
!sudo apt-get install tree

Reading package lists... Done
Building dependency tree       
Reading state information... Done
tree is already the newest version (1.7.0-5).
0 upgraded, 0 newly installed, 0 to remove and 40 not upgraded.


In [30]:
!tree

.
├── AudioTech One-Pager.gdoc
├── demo_cli.py
├── demo_toolbox.py
├── encoder
│   ├── audio.py
│   ├── config.py
│   ├── data_objects
│   │   ├── __init__.py
│   │   ├── random_cycler.py
│   │   ├── speaker_batch.py
│   │   ├── speaker.py
│   │   ├── speaker_verification_dataset.py
│   │   └── utterance.py
│   ├── inference.py
│   ├── __init__.py
│   ├── model.py
│   ├── params_data.py
│   ├── params_model.py
│   ├── preprocess.py
│   ├── __pycache__
│   │   ├── audio.cpython-37.pyc
│   │   ├── inference.cpython-37.pyc
│   │   ├── __init__.cpython-37.pyc
│   │   ├── model.cpython-37.pyc
│   │   ├── params_data.cpython-37.pyc
│   │   └── params_model.cpython-37.pyc
│   ├── saved_models
│   │   └── pretrained.pt
│   ├── train.py
│   └── visualizations.py
├── encoder_preprocess.py
├── encoder_train.py
├── LICENSE.txt
├── pa_stable_v190700_20210406.tgz
├── pretrained.zip
├── pretrained.zip.1
├── pretrained.zip.2
├── README.md
├── requirements.txt
├── samples
│   ├── 1320_00000.mp3
│   ├──

In [31]:
!pip install ipdb
!pip install matplotlib

In [32]:
from encoder import inference as encoder
from synthesizer.inference import Synthesizer
from vocoder import inference as vocoder
from pathlib import Path
from time import perf_counter as timer
from toolbox.utterance import Utterance
import numpy as np
import traceback
import sys
import torch
import librosa
from audioread.exceptions import NoBackendError
 
ENCODER_PATH = Path("encoder/saved_models/pretrained.pt")
SYNTHESIZER_PATH = Path("synthesizer/saved_models/pretrained/pretrained.pt")
VOCODER_PATH = Path("vocoder/saved_models/pretrained/pretrained.pt")
encoder.load_model(ENCODER_PATH)
synthesizer = Synthesizer(SYNTHESIZER_PATH)
vocoder.load_model(VOCODER_PATH)


Loaded encoder "pretrained.pt" trained to step 1564501
Synthesizer using device: cuda
Building Wave-RNN
Trainable Parameters: 4.481M
Loading model weights at vocoder/saved_models/pretrained/pretrained.pt


In [33]:
avg_embed = np.zeros((256,))

#text = ['One of the two people who tested positive for the novel coronavirus in the United Kingdom is a student at the University of York in northern England.']
text = ['Rachel Lynn is surprised. Miss Rachel Lynde lived just where the Avonlea Main Road, dipped down into a little hollow fringed with alders and ladies eardrops and traversed by a brook.']

#text =['we describe a neural network-based system for text-to-speech synthesis that is able to generate speech audio in the voice of different speakers, including those unseen during training.']
# text = ['hi there, it is nice to meet you all.']
# to do: turn embedding into mean
for wav in other_wavs:
  wav = np.squeeze(np.array(wav))
  # wav = np.expand_dims(np.array(target_wav),1)
  # print(wav.shape)
  encoder_wav = encoder.preprocess_wav(wav)
  # print(encoder_wav.shape)
  # import ipdb; ipdb.set_trace()
  # embed, partial_embeds, _ = encoder.embed_utterance(wav, return_partials=True)

  embed = encoder.embed_utterance(encoder_wav)
  # print(embed.shape)
  # embed = np.expand_dims(embed,0)
  # print(embed.shape)
  avg_embed += embed / len(other_wavs)

# embed, partial_embeds, _ = encoder.embed_utterance(encoder_wav, return_partials=True)
spec = synthesizer.synthesize_spectrograms(text, avg_embed)

# two ways to transform spectrogram to audio
generated_wav = vocoder.infer_waveform(spec[0])
# or 
# generated_wav = Synthesizer.griffin_lim(spec)

Trainable Parameters: 30.870M
Loaded synthesizer "pretrained.pt" trained to step 295000
+----------+---+
| Tacotron | r |
+----------+---+
|   295k   | 2 |
+----------+---+
 

| Generating 1/1


Done.

{| ████████████████ 133000/134400 | Batch Size: 14 | Gen Rate: 13.1kHz | }

In [34]:
target_wav.shape

torch.Size([1, 240000])

In [35]:
play_audio(target_wav,16000)

In [36]:
generated_wav.shape

(117600,)

In [37]:
play_audio(np.expand_dims(generated_wav, axis = 0),16000)

In [38]:
len(other_wavs)


3

In [39]:
play_audio(other_wavs[0],16000)

In [40]:
play_audio(other_wavs[1],16000)

In [41]:
play_audio(other_wavs[2],16000)